In [ ]:
# get markers?

In [2]:
library(Seurat)
library(dplyr)
library(SingleCellExperiment)
library(MetaMarkers)

In [3]:
sc1 = readRDS('Kanemaru_data.rds')
sc1

An object of class Seurat 
32583 features across 704296 samples within 1 assay 
Active assay: RNA (32583 features, 0 variable features)
 2 layers present: counts, data
 1 dimensional reduction calculated: umap

In [4]:
mtd = sc1@meta.data
exp1 = LayerData(sc1, assay = 'RNA', layer = 'counts')
mtd[1:2,]

sangerID        donor_type region age  
HCAHeart7606896_GATGAGGCACGGCTAC HCAHeart7606896 DBD        AX     50-55
HCAHeart7606896_CGCTTCACATTTGCCC HCAHeart7606896 DBD        AX     50-55
                                 facility flushed cell_state nFeaturess_RNA
HCAHeart7606896_GATGAGGCACGGCTAC Sanger   no      EC5_art    2470          
HCAHeart7606896_CGCTTCACATTTGCCC Sanger   no      SMC2_art   2057          
                                 nFeaturess_RNA_by_counts total_counts ⋯
HCAHeart7606896_GATGAGGCACGGCTAC 2470                     7127         ⋯
HCAHeart7606896_CGCTTCACATTTGCCC 2057                     6094         ⋯
                                 tissue_type cell_type        assay     disease
HCAHeart7606896_GATGAGGCACGGCTAC tissue      endothelial cell 10x 3' v2 normal 
HCAHeart7606896_CGCTTCACATTTGCCC tissue      mural cell       10x 3' v2 normal 
                                 organism     sex    tissue       
HCAHeart7606896_GATGAGGCACGGCTAC Homo sapiens female apex of heart
HCAHeart7606896_CGCTTCACATTTGCCC Homo sapiens female apex of heart
                                 self_reported_ethnicity development_stage 
HCAHeart7606896_GATGAGGCACGGCTAC European                sixth decade stage
HCAHeart7606896_CGCTTCACATTTGCCC European                sixth decade stage
                                 observation_joinid
HCAHeart7606896_GATGAGGCACGGCTAC yA%bjGu4uL        
HCAHeart7606896_CGCTTCACATTTGCCC IPCWGLNh{t

In [9]:
head(mtd %>% group_by(cell_type, cell_state) %>% reframe(count = n()), n = 10)

cell_type                           cell_state      count
1  regular atrial cardiac myocyte      SAN_P_cell        245
2  regular atrial cardiac myocyte      AVN_P_cell        155
3  regular atrial cardiac myocyte      AVN_bundle_cell    38
4  regular atrial cardiac myocyte      aCM1            18269
5  regular atrial cardiac myocyte      aCM2            14452
6  regular atrial cardiac myocyte      aCM3             5701
7  regular atrial cardiac myocyte      aCM4             6729
8  regular atrial cardiac myocyte      aCM5               55
9  regular atrial cardiac myocyte      unclassified      267
10 regular ventricular cardiac myocyte Purkinje          110

In [5]:
table(mtd$cell_type)


      regular atrial cardiac myocyte  regular ventricular cardiac myocyte 
                               45911                               190710 
                          fibroblast                     endothelial cell 
                              138055                               131505 
endothelial cell of lymphatic vessel                           mural cell 
                                1295                               104593 
                    mesothelial cell                          neural cell 
                                1057                                 6622 
                           adipocyte                         myeloid cell 
                                6347                                51426 
                          lymphocyte                            mast cell 
                               24922                                 1853 

In [7]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = exp1), colData = DataFrame(mtd))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [17]:
# get cell type markers on whole data
# markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$cell_type)
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$cell_state, 
                          group_labels = sce2$cell_type)
head(markers)

group            cell_type     gene            fold_change auroc    
1 endothelial cell EC10_CMC-like ENSG00000163638 4.273305    0.7192346
2 endothelial cell EC10_CMC-like ENSG00000117461 4.475803    0.6891181
3 endothelial cell EC10_CMC-like ENSG00000187498 3.970269    0.6684709
4 endothelial cell EC10_CMC-like ENSG00000134871 3.945717    0.6584024
5 endothelial cell EC10_CMC-like ENSG00000126217 2.308884    0.6488557
6 endothelial cell EC10_CMC-like ENSG00000251322 2.361148    0.6480686
  log_fdr    population_size population_fraction average_expression
1 -1594.7936 5793            0.04405156          5371.0094         
2 -1186.4566 5793            0.04405156          1982.6459         
3  -941.3444 5793            0.04405156          1184.1782         
4  -832.0977 5793            0.04405156          1107.1733         
5  -734.7243 5793            0.04405156           684.0806         
6  -726.9688 5793            0.04405156           647.0106         
  se_expression detection_rate fold_change_detection precision  recall   
1 107.45681     0.7578112      1.611980              0.06919815 0.7578112
2  42.71505     0.6621785      1.663872              0.07127992 0.6621785
3  27.47330     0.5983083      1.758778              0.07505901 0.5983083
4  25.96394     0.5584326      1.825277              0.07769159 0.5584326
5  12.09519     0.5998619      1.711283              0.07317484 0.5998619
6  11.98227     0.5877784      1.743916              0.07447181 0.5877784

In [14]:
# convert gene names to symbols
ginfo = read.delim('~/bican/cross_species/Sepp/human/human_ens_symbol.txt', sep = '\t')
ginfo <- ginfo[ginfo[,1]!='' & ginfo[,2]!='',]
dim(ginfo)
ginfo[1,]

[1] 48379     2

Gene.stable.ID  Gene.name
1 ENSG00000210049 MT-TF

In [18]:
# remove genes w/o symbols
markers$gene <- ginfo[match(markers$gene, ginfo[,1]),2]
dim(markers)
markers <- markers[!is.na(markers$gene),]
dim(markers)

head(markers[markers$cell_type=='aCM1',])

[1] 2834721      14

[1] 2155512      14

group                          cell_type gene       fold_change auroc    
1 regular atrial cardiac myocyte aCM1      MALAT1     1.537563    0.6773288
2 regular atrial cardiac myocyte aCM1      KCNMB2-AS1 2.236169    0.6344696
3 regular atrial cardiac myocyte aCM1      LINC02147  1.754903    0.6072391
4 regular atrial cardiac myocyte aCM1      EPHA5      3.306752    0.6041242
5 regular atrial cardiac myocyte aCM1      PLCB1      1.813187    0.6023233
6 regular atrial cardiac myocyte aCM1      FGF12      1.267452    0.5903614
  log_fdr    population_size population_fraction average_expression
1 -2070.7284 18269           0.3979221           174424.1316       
2 -1190.0526 18269           0.3979221              815.4878       
3  -756.4565 18269           0.3979221              831.8759       
4  -713.1144 18269           0.3979221              114.2520       
5  -688.6353 18269           0.3979221              490.8630       
6  -536.9338 18269           0.3979221             6386.6047       
  se_expression detection_rate fold_change_detection precision recall   
1 838.158982    0.9995621      1.033979              0.4059624 0.9995621
2   8.237618    0.7069352      1.237147              0.4499216 0.7069352
3   7.953566    0.6987794      1.165706              0.4352243 0.6987794
4   1.818849    0.3058186      3.046757              0.6696632 0.3058186
5   4.754481    0.6253763      1.166524              0.4354040 0.6253763
6  32.098574    0.9630522      1.023454              0.4034951 0.9630522

In [19]:
# save marker list
export_meta_markers(markers, "Kanemaru_celltype_markers_res3.csv", names(markers))